In [1]:
import json
from typing import List, Optional, Dict

import uvicorn
from fastapi import FastAPI, Request, Depends
from pydantic import BaseModel
from contextlib import asynccontextmanager

In [2]:
import re
import json
from typing import List, Optional, Dict, Tuple
from functools import lru_cache

class LawLink(BaseModel):
    law_id: Optional[int] = None
    article: Optional[str] = None
    point_article: Optional[str] = None
    subpoint_article: Optional[str] = None


class LinksResponse(BaseModel):
    links: List[LawLink]


class TextRequest(BaseModel):
    text: str

class LawLinkExtractor:
    def __init__(self, law_aliases: Dict):
        self.law_aliases = law_aliases
        self.patterns = self._build_patterns()
        
    def _build_patterns(self) -> List[Tuple[re.Pattern, str]]:
        """Создает regex паттерны для распознавания ссылок"""
        
        # Паттерны для разных компонентов ссылки
        subpoint_pattern = r'(?:подпункт|подп|пп)\.?\s*([а-яё\d,\s\.\-и]+)'
        point_pattern = r'(?:пункт|п|пункта)\.?\s*([\d\w\s,\-\.и]+)'
        article_pattern = r'(?:статья|ст|статьи)\.?\s*([\d\w\s,\-\.и]+)'
        
        # Основные паттерны ссылок (от самого специфичного к общему)
        patterns = [
            # Полная ссылка с подпунктом
            (
                re.compile(
                    rf'{subpoint_pattern}\s+{point_pattern}\s+{article_pattern}\s+([^,\.;]+)',
                    re.IGNORECASE
                ),
                'full_with_subpoint'
            ),
            # Ссылка с пунктом и статьей
            (
                re.compile(
                    rf'{point_pattern}\s+{article_pattern}\s+([^,\.;]+)',
                    re.IGNORECASE
                ),
                'with_point'
            ),
            # Просто статья и закон
            (
                re.compile(
                    rf'{article_pattern}\s+([^,\.;]+)',
                    re.IGNORECASE
                ),
                'article_only'
            ),
        ]
        return patterns
    
    @lru_cache(maxsize=1000)
    def find_law_id(self, law_name: str) -> Optional[int]:
        """Находит law_id по названию закона"""
        law_name_clean = law_name.strip().lower()
        
        for law_id, aliases in self.law_aliases.items():
            for alias in aliases:
                if alias.lower() in law_name_clean or law_name_clean in alias.lower():
                    return int(law_id)
        return None
    
    def parse_article_parts(self, text: str) -> List[str]:
        """Парсит перечисления типа '1, 2, 3' или 'а, б, в'"""
        if not text:
            return []
        
        # Очистка текста
        clean_text = re.sub(r'\s+', ' ', text.strip())
        
        # Разделение по запятым, "и", пробелам
        parts = re.split(r'[,\sи]+', clean_text)
        
        # Фильтрация пустых значений и нормализация
        result = []
        for part in parts:
            part = part.strip()
            if part and part not in ['', 'и']:
                # Убираем лишние точки в конце
                if part.endswith('.'):
                    part = part[:-1]
                result.append(part)
                
        return result
    
    def extract_links(self, text: str) -> List[LawLink]:
        """Основной метод извлечения ссылок из текста"""
        links = []
        
        for pattern, pattern_type in self.patterns:
            matches = pattern.findall(text)
            
            for match in matches:
                if pattern_type == 'full_with_subpoint':
                    subpoint_text, point_text, article_text, law_text = match
                    law_id = self.find_law_id(law_text)
                    
                    # Обрабатываем множественные подпункты
                    subpoints = self.parse_article_parts(subpoint_text)
                    points = self.parse_article_parts(point_text)
                    articles = self.parse_article_parts(article_text)
                    
                    if subpoints:
                        for subpoint in subpoints:
                            links.append(LawLink(
                                law_id=law_id,
                                article=articles[0] if articles else None,
                                point_article=points[0] if points else None,
                                subpoint_article=subpoint
                            ))
                    else:
                        links.append(LawLink(
                            law_id=law_id,
                            article=articles[0] if articles else None,
                            point_article=points[0] if points else None,
                            subpoint_article=None
                        ))
                        
                elif pattern_type == 'with_point':
                    point_text, article_text, law_text = match
                    law_id = self.find_law_id(law_text)
                    
                    points = self.parse_article_parts(point_text)
                    articles = self.parse_article_parts(article_text)
                    
                    if points:
                        for point in points:
                            links.append(LawLink(
                                law_id=law_id,
                                article=articles[0] if articles else None,
                                point_article=point,
                                subpoint_article=None
                            ))
                    else:
                        links.append(LawLink(
                            law_id=law_id,
                            article=articles[0] if articles else None,
                            point_article=None,
                            subpoint_article=None
                        ))
                        
                elif pattern_type == 'article_only':
                    article_text, law_text = match
                    law_id = self.find_law_id(law_text)
                    
                    articles = self.parse_article_parts(article_text)
                    
                    if articles:
                        for article in articles:
                            links.append(LawLink(
                                law_id=law_id,
                                article=article,
                                point_article=None,
                                subpoint_article=None
                            ))
        
        return links

In [3]:
with open('homework_1/law_aliases.json', 'r') as f:
    law_aliases = json.load(f)

In [5]:
ex = LawLinkExtractor(law_aliases=law_aliases)

In [4]:
itext = """
В соответствии с пп. 1 п. 1 ст. 374 НК РФ объектами налогообложения признается недвижимое имущество, 
учитываемое на балансе организации в качестве объектов основных средств в порядке, установленном для ст. 105 УК РФ и ведения бухгалтерского учета, в случае, если налоговая база в отношении такого имущества определяется как его среднегодовая стоимость. Согласно п.  10 АПК для целей бухгалтерского учета по общему правилу единицей учета основных средств является инвентарный объект.

Согласно статье 17 Конституции Российской Федерации, каждый гражданин имеет право на жизнь и свободу. Однако, в соответствии с п. 5 ст. 105 УК РФ, убийство двух или более лиц наказывается лишением свободы на срок до двадцати лет. Также, п. 3 ст. 158 УК РФ предусматривает наказание за кражу, совершенную группой лиц по предварительному сговору. Важно отметить, что согласно ст. 30 Гражданского кодекса Российской Федерации, гражданин, признанный недееспособным, не может самостоятельно заключать сделки.
В соответствии с пп. 12 п. 4 ст. 159 УК РФ, мошенничество, совершенное в крупном размере, наказывается лишением свободы на срок до десяти лет. Согласно п. 2 ст. 228 УК РФ, незаконное хранение лабуб в особо крупном размере карается лишением свободы на срок до пятнадцати лет. Необходимо упомянуть и ст. 275 Налогового Кодекса Российской Федерации, которая регулирует порядок налогообложения прибыли контролируемых иностранных компаний.
Согласно ст. 90 Семейного кодекса Российской Федерации, алименты могут быть взысканы в судебном порядке. Также, ст. 70 Трудового кодекса Российской Федерации определяет порядок заключения трудового договора. В соответствии с п. 1 ст. 213 Гражданского процессуального кодекса Российской Федерации, судебные решения подлежат немедленному исполнению.
Важно учитывать, что согласно пункта а ст. 20 АПК, запрещены действия, направленные на ограничение конкуренции. Согласно статье 16 Закона "О защите прав потребителей", продавец обязан предоставить покупателю полную и достоверную информацию о товаре. В соответствии с п. 2 ст. 14 Закона "О персональных данных", оператор обязан обеспечить конфиденциальность персональных данных.
Согласно ст. 19 Федерального закона "О бухгалтерском учёте", бухгалтерский учёт обязателен для всех организаций. Важно отметить, что согласно п. р ст. 9 Федерального закона "О государственной регистрации юридических лиц и индивидуальных предпринимателей", регистрация изменений в учредительных документах юридического лица осуществляется в течение пяти рабочих дней. В соответствии с п. 1 ст. 16 Закона "О защите прав юридических лиц и индивидуальных предпринимателей при осуществлении государственного контроля (надзора) и муниципального контроля", плановые проверки проводятся не чаще одного раза в три года.
Согласно подпункту 2 пунта б статьи 22 Федерального закона "О государственной гражданской службе Российской Федерации", гражданский служащий обязан соблюдать служебную дисциплину. Важно учитывать, что согласно ст. 12 Федерального закона "О защите конкуренции", запрещено злоупотребление доминирующим положением на рынке. Согласно п. 3 статьи 20 Федерального закона "О полиции", полицейские обязаны действовать в строгом соответствии с законодательством Российской Федерации.
Согласно ст. 37 ФЗ №20-456, прокурор вправе вносить представления об устранении нарушений закона. В соответствии с пп. 4, 5, 6 и 8 п. 1 ст. 14 Федерального закона "О государственной регистрации недвижимости", сведения о правах на недвижимость вносятся в Единый государственный реестр недвижимости. Важно отметить, что согласно ст. 6 Федерального закона "О банках и банковской деятельности", банки обязаны соблюдать банковскую тайну.

В пункте 1 статьи 34 Гражданского Кодекса такого не было.
А в пп. 1 п. 2 ст. 34 рандомного кодекса было всё.
Таким образом, в подпунктах а, б и с пункта 3.345, 23 в статье 66 НК РФ Ничего такого и не было.

Дополнительно для процесса обжалования применяются общие правила часть 3, ст. 30.1 КоАП РФ (постановления об административных правонарушениях обжалуются в суд), при дальнейшем споре — нормы ст. 211 АПК РФ и далее.
"""

In [5]:
s = """
хуй пп. 1 п. 2 ст. 374 НК РФ хуйххуйх
ст. 105 УК РФ
п.  10 АПК
статье 17 Конституции Российской Федерации
п. 5 ст. 105 УК РФ
п. 3 ст. 158 УК РФ
ст. 30 Гражданского кодекса Российской Федерации
пп. 12 п. 4 ст. 159 УК РФ
п. 2 ст. 228 УК РФ
ст. 275 Налогового Кодекса Российской Федерации
ст. 90 Семейного кодекса Российской Федерации
ст. 70 Трудового кодекса Российской Федерации
п. 1 ст. 213 Гражданского процессуального кодекса Российской Федерации
ст. 20 АПК
статье 16 Закона "О защите прав потребителей"
п. 2 ст. 14 Закона "О персональных данных"
ст. 19 Федерального закона "О бухгалтерском учёте"
подпункту 2 пунта б статьи 22 Федерального закона "О государственной гражданской службе Российской Федерации"
ст. 12 Федерального закона "О защите конкуренции"
п. 3 статьи 20 Федерального закона "О полиции"
ст. 37 ФЗ №20-456
пп. 4, 5, 6 и 8 п. 1 ст. 14 Федерального закона "О государственной регистрации недвижимости"
ст. 6 Федерального закона "О банках и банковской деятельности"
пункте 1 статьи 34 Гражданского Кодекса
пп. 1 п. 2 ст. 34
подпунктах а, б и с пункта 3.345, 23 в статье 66 НК РФ
часть 3, ст. 30.1 КоАП РФ
ст. 211 АПК РФ
"""

In [160]:
aricle_pattern = re.compile(r'(.*?)(ст\.|статье|статьи|статья)(.*)')
article_number_pattern = re.compile(r'\s*[\.\d]+')
point_number_pattern = re.compile(r'\s(?:п\.|пункта|пункт|часть|части)\s(\d+)')

for row in s.split('\n')[:2]:
    if row:
        match = re.search(aricle_pattern, row)

        if match:
            before_article = match.group(1)    # "монтаж оборудования "
            article = match.group(2)    # "подпункт"  
            after_article = match.group(3) # " 1.2 установка систем"
            article_number = article_number_pattern.findall(after_article)[0]
            point_number = point_number_pattern.findall(before_article)[0]
            print(before_article, ' - ', article, ' - ', after_article)
            print(
                f'Article: {article_number}, '
                f'Point: {point_number}'
            )

хуй пп. 1 п. 2   -  ст.  -   374 НК РФ хуйххуйх
Article:  374, Point: 2


In [172]:
s1 = 'подпунктах а, б и с пункта 3.345, 23 в статье 66 НК РФ'
subpoint_number_pattern = re.compile(r'\s?(?:пп\.|подпункту|подпункт|подпунктах)[а-я\s,]+\s')
subpoint_number_pattern.findall(s1)

['подпунктах а, б и с пункта ']

In [10]:
import pymorphy3
morph = pymorphy3.MorphAnalyzer()

In [11]:
normalized_text = ' '.join(morph.parse(item)[0].normal_form for item in s.split())
normalized_text


'хуй пп. 1 п. 2 ст. 374 нк рф хуйххуйх ст. 105 ук рф п. 10 апк статья 17 конституция российский федерация п. 5 ст. 105 ук рф п. 3 ст. 158 ук рф ст. 30 гражданский кодекс российский федерация пп. 12 п. 4 ст. 159 ук рф п. 2 ст. 228 ук рф ст. 275 налоговый кодекс российский федерация ст. 90 семейный кодекс российский федерация ст. 70 трудовой кодекс российский федерация п. 1 ст. 213 гражданский процессуальный кодекс российский федерация ст. 20 апк статья 16 закон "о защита право потребителей" п. 2 ст. 14 закон "о персональный данных" ст. 19 федеральный закон "о бухгалтерский учёте" подпункт 2 пунт б статья 22 федеральный закон "о государственный гражданский служба российский федерации" ст. 12 федеральный закон "о защита конкуренции" п. 3 статья 20 федеральный закон "о полиции" ст. 37 фз №20-456 пп. 4, 5, 6 и 8 п. 1 ст. 14 федеральный закон "о государственный регистрация недвижимости" ст. 6 федеральный закон "о банк и банковский деятельности" пункт 1 статья 34 гражданский кодекс пп. 1 п. 2

In [620]:
aricle_pattern = re.compile(r'(?:ст\.|статья)\s*([\.\d]+)')
aricle_point_pattern = re.compile(
    r'\s*([\d]+)\s*'
    r'(?:ст\.|статья)\s*([\.\d]+)'
)
aricle_point_subpoint_pattern = re.compile(
    r'\s*([\d]+)\s*(?:п\.|пункт)'
    r'\s*([\d]+)\s*'
    r'(?:ст\.|статья)\s*([\.\d]+)'
    
)
article_source_pattern = re.compile(
    # r'([а-яё\s]*?)(?:ст\.|статья)\s*([\.\d]+)([а-яё\s]*)?'
    r'([а-яё\s]*?)(?:ст\.|статья)\s*([\.\d]+)([а-яё\s]*)'
)
article_point_subpoint_source_pattern = re.compile(
    r'\s*(?:пп\.|подпункт)\s*([\d]+)'
    r'\s*(?:\sп\.|пункт)\s*([\d]+)\s*'
    r'(?:\s+ст\.|статья)\s*([\d]+)'
    # r'([а-яё\s]*?)(?:ст\.|статья)\s*([\.\d]+)([а-яё\s]*)'
)
article_point_source_pattern = re.compile(
    # r'\s*(?:пп\.|подпункт)\s*([\d]+)'
    r'\s*(?:\sп\.|пункт)\s*([\d]+)\s*'
    r'(?:\s+ст\.|статья)\s*([\d]+)'
)
article_source_pattern = re.compile(
    # r'\s*(?:пп\.|подпункт)\s*([\d]+)'
    # r'(?:\s+ст\.|статья)\s*([\d]+)'
    # r'(.*?)(?:\s+ст\.|статья|\s+п\.|\s+пп\.|$)',
    r'\s*(?:пп\.|подпункт)\s*([\d]+)'
    r'\s*(?:\sп\.|пункт)\s*([\d]+)\s*'
    r'(?:ст\.|статья)\s*(\d+[\.\d]*)\s*'
    r'(.*?)'
    r'(?=\s*(?:ст\.|статья|п\.|пп\.|$))',
    re.IGNORECASE
)


article_number_pattern = re.compile(r'\s*[\.\d]+')
point_number_pattern = re.compile(r'\s(?:п\.|пункта|пункт|часть|части)\s(\d+)')

In [10]:
import pymorphy3
morph = pymorphy3.MorphAnalyzer()

In [11]:
normalized_text = ' '.join(morph.parse(item)[0].normal_form for item in s.split())
normalized_text


'хуй пп. 1 п. 2 ст. 374 нк рф хуйххуйх ст. 105 ук рф п. 10 апк статья 17 конституция российский федерация п. 5 ст. 105 ук рф п. 3 ст. 158 ук рф ст. 30 гражданский кодекс российский федерация пп. 12 п. 4 ст. 159 ук рф п. 2 ст. 228 ук рф ст. 275 налоговый кодекс российский федерация ст. 90 семейный кодекс российский федерация ст. 70 трудовой кодекс российский федерация п. 1 ст. 213 гражданский процессуальный кодекс российский федерация ст. 20 апк статья 16 закон "о защита право потребителей" п. 2 ст. 14 закон "о персональный данных" ст. 19 федеральный закон "о бухгалтерский учёте" подпункт 2 пунт б статья 22 федеральный закон "о государственный гражданский служба российский федерации" ст. 12 федеральный закон "о защита конкуренции" п. 3 статья 20 федеральный закон "о полиции" ст. 37 фз №20-456 пп. 4, 5, 6 и 8 п. 1 ст. 14 федеральный закон "о государственный регистрация недвижимости" ст. 6 федеральный закон "о банк и банковский деятельности" пункт 1 статья 34 гражданский кодекс пп. 1 п. 2

In [29]:
patterns = {
    'article': r'(?:ст\.|статья)\s*(\d+[\.\d]*)\s*',
    'source': r'(.*?)(?=\s*(?:ст\.|статья|п\.|пп\.|$))',
    'point': r'\s*(?:\sп\.|пункт)\s*([\d]+)\s*',
    'subpoint': r'\s*(?:пп\.|подпункт)\s*([\d]+)',
}
patterns_combinations = [
    ('subpoint', 'point', 'article', 'source'),
    ('point', 'article', 'source'),
    ('article', 'source'),
    ('point', 'source'),
]

In [36]:
text_corpus = normalized_text[:300] + '.'
text_corpus

'хуй пп. 1 п. 2 ст. 374 нк рф хуйххуйх ст. 105 ук рф п. 10 апк статья 17 конституция российский федерация п. 5 ст. 105 ук рф п. 3 ст. 158 ук рф ст. 30 гражданский кодекс российский федерация пп. 12 п. 4 ст. 159 ук рф п. 2 ст. 228 ук рф ст. 275 налоговый кодекс российский федерация ст. 90 семейный код.'

In [37]:
found
for combination in patterns_combinations:
    combination_pattern = re.compile(''.join(patterns[item] for item in combination))
    print(combination_pattern.findall(text_corpus))

[('1', '2', '374', 'нк рф хуйххуйх'), ('12', '4', '159', 'ук рф')]
[('2', '374', 'нк рф хуйххуйх'), ('5', '105', 'ук рф'), ('3', '158', 'ук рф'), ('4', '159', 'ук рф'), ('2', '228', 'ук рф')]
[('374', 'нк рф хуйххуйх'), ('105', 'ук рф'), ('17', 'конституция российский федерация'), ('105', 'ук рф'), ('158', 'ук рф'), ('30', 'гражданский кодекс российский федерация'), ('159', 'ук рф'), ('228', 'ук рф'), ('275', 'налоговый кодекс российский федерация'), ('90', 'семейный код.')]
[('2', ''), ('10', 'апк'), ('5', ''), ('3', ''), ('4', ''), ('2', '')]


In [ ]:
class LawLink(BaseModel):
    law_id: Optional[int] = None
    article: Optional[str] = None
    point_article: Optional[str] = None
    subpoint_article: Optional[str] = None

In [25]:
patterns.values()

dict_values(['(?:ст\\.|статья)\\s*(\\d+[\\.\\d]*)\\s*', '(.*?)(?=\\s*(?:ст\\.|статья|п\\.|пп\\.|$))', '\\s*(?:\\sп\\.|пункт)\\s*([\\d]+)\\s*', '\\s*(?:пп\\.|подпункт)\\s*([\\d]+)'])

In [27]:
sum(list(patterns.values()))

TypeError: unsupported operand type(s) for +: 'int' and 'str'

In [13]:
article_source_pattern = re.compile(patterns['article'] + patterns['source'])
point_article_source_pattern = re.compile(
    patterns['point'] 
    + patterns['article'] 
    + patterns['source']
)
subpoint_point_article_source_pattern = re.compile(
    patterns['subpoint'] 
    + patterns['point'] 
    + patterns['article'] 
    + patterns['source']
)
point_source_pattern = re.compile(patterns['point'] + patterns['source'])


In [14]:
part = normalized_text[:300] + '.'
part

'хуй пп. 1 п. 2 ст. 374 нк рф хуйххуйх ст. 105 ук рф п. 10 апк статья 17 конституция российский федерация п. 5 ст. 105 ук рф п. 3 ст. 158 ук рф ст. 30 гражданский кодекс российский федерация пп. 12 п. 4 ст. 159 ук рф п. 2 ст. 228 ук рф ст. 275 налоговый кодекс российский федерация ст. 90 семейный код.'

In [15]:
subpoint_point_article_source_pattern.findall(part)

[('1', '2', '374', 'нк рф хуйххуйх'), ('12', '4', '159', 'ук рф')]

In [16]:
point_article_source_pattern.findall(part)

[('2', '374', 'нк рф хуйххуйх'),
 ('5', '105', 'ук рф'),
 ('3', '158', 'ук рф'),
 ('4', '159', 'ук рф'),
 ('2', '228', 'ук рф')]

In [17]:
article_source_pattern.findall(part)

[('374', 'нк рф хуйххуйх'),
 ('105', 'ук рф'),
 ('17', 'конституция российский федерация'),
 ('105', 'ук рф'),
 ('158', 'ук рф'),
 ('30', 'гражданский кодекс российский федерация'),
 ('159', 'ук рф'),
 ('228', 'ук рф'),
 ('275', 'налоговый кодекс российский федерация'),
 ('90', 'семейный код.')]

In [18]:
point_source_pattern.findall(part)

[('2', ''), ('10', 'апк'), ('5', ''), ('3', ''), ('4', ''), ('2', '')]

In [20]:
normalized_text_test = ''
normalized_text_test = ' '.join(morph.parse(item)[0].normal_form for item in itext.replace('\n', ' ').split())
print(normalized_text_test)


в соответствие с пп. 1 п. 1 ст. 374 нк рф объект налогообложение признаваться недвижимый имущество, учитывать на баланс организация в качество объект основный средство в порядке, установить для ст. 105 ук рф и ведение бухгалтерский учета, в случае, если налоговый база в отношение такой имущество определяться как он среднегодовой стоимость. согласно п. 10 апк для цель бухгалтерский учёт по общий правило единица учёт основный средство являться инвентарный объект. согласно статья 17 конституция российский федерации, каждый гражданин иметь право на жизнь и свободу. однако, в соответствие с п. 5 ст. 105 ук рф, убийство два или более лицо наказываться лишение свобода на срок до двадцать лет. также, п. 3 ст. 158 ук рф предусматривать наказание за кражу, совершенный группа лицо по предварительный сговору. важно отметить, что согласно ст. 30 гражданский кодекс российский федерации, гражданин, признанный недееспособным, не мочь самостоятельно заключать сделки. в соответствие с пп. 12 п. 4 ст. 15

In [23]:
print(s)



хуй пп. 1 п. 2 ст. 374 НК РФ хуйххуйх
ст. 105 УК РФ
п.  10 АПК
статье 17 Конституции Российской Федерации
п. 5 ст. 105 УК РФ
п. 3 ст. 158 УК РФ
ст. 30 Гражданского кодекса Российской Федерации
пп. 12 п. 4 ст. 159 УК РФ
п. 2 ст. 228 УК РФ
ст. 275 Налогового Кодекса Российской Федерации
ст. 90 Семейного кодекса Российской Федерации
ст. 70 Трудового кодекса Российской Федерации
п. 1 ст. 213 Гражданского процессуального кодекса Российской Федерации
ст. 20 АПК
статье 16 Закона "О защите прав потребителей"
п. 2 ст. 14 Закона "О персональных данных"
ст. 19 Федерального закона "О бухгалтерском учёте"
подпункту 2 пунта б статьи 22 Федерального закона "О государственной гражданской службе Российской Федерации"
ст. 12 Федерального закона "О защите конкуренции"
п. 3 статьи 20 Федерального закона "О полиции"
ст. 37 ФЗ №20-456
пп. 4, 5, 6 и 8 п. 1 ст. 14 Федерального закона "О государственной регистрации недвижимости"
ст. 6 Федерального закона "О банках и банковской деятельности"
пункте 1 статьи 34

In [27]:
found = article_source_pattern.findall(normalized_text_test)
for i, item in enumerate(s.split('\n')[1:-1]):
    print(item, '  ===  ', found[i])
    print()

хуй пп. 1 п. 2 ст. 374 НК РФ хуйххуйх   ===   ('374', 'нк рф объект налогообложение признаваться недвижимый имущество, учитывать на баланс организация в качество объект основный средство в порядке, установить для')

ст. 105 УК РФ   ===   ('105', 'ук рф и ведение бухгалтерский учета, в случае, если налоговый база в отношение такой имущество определяться как он среднегодовой стоимость. согласно')

п.  10 АПК   ===   ('17', 'конституция российский федерации, каждый гражданин иметь право на жизнь и свободу. однако, в соответствие с')

статье 17 Конституции Российской Федерации   ===   ('105', 'ук рф, убийство два или более лицо наказываться лишение свобода на срок до двадцать лет. также,')

п. 5 ст. 105 УК РФ   ===   ('158', 'ук рф предусматривать наказание за кражу, совершенный группа лицо по предварительный сговору. важно отметить, что согласно')

п. 3 ст. 158 УК РФ   ===   ('30', 'гражданский кодекс российский федерации, гражданин, признанный недееспособным, не мочь самостоятельно заклю

In [21]:
article_source_pattern.findall(normalized_text_test)

[('374',
  'нк рф объект налогообложение признаваться недвижимый имущество, учитывать на баланс организация в качество объект основный средство в порядке, установить для'),
 ('105',
  'ук рф и ведение бухгалтерский учета, в случае, если налоговый база в отношение такой имущество определяться как он среднегодовой стоимость. согласно'),
 ('17',
  'конституция российский федерации, каждый гражданин иметь право на жизнь и свободу. однако, в соответствие с'),
 ('105',
  'ук рф, убийство два или более лицо наказываться лишение свобода на срок до двадцать лет. также,'),
 ('158',
  'ук рф предусматривать наказание за кражу, совершенный группа лицо по предварительный сговору. важно отметить, что согласно'),
 ('30',
  'гражданский кодекс российский федерации, гражданин, признанный недееспособным, не мочь самостоятельно заключать сделки. в соответствие с'),
 ('159',
  'ук рф, мошенничество, совершенный в крупный размере, наказываться лишение свобода на срок до десять лет. согласно'),
 ('228',
  '

In [647]:
subpoint_point_article_source_pattern.findall(itext.split('\n')[13])

[('1', '2', '34', 'рандомного кодекса было всё.')]

In [ ]:
itext

In [622]:
l = article_source_pattern.findall(part)
l

[('1', '2', '374', 'нк рф хуйххуйх'), ('12', '4', '159', 'ук рф')]

In [533]:
len(l[0])

2

In [374]:
part = itext.split('\n')[2]
part

'учитываемое на балансе организации в качестве объектов основных средств в порядке, установленном для ст. 105 УК РФ и ведения бухгалтерского учета, в случае, если налоговая база в отношении такого имущества определяется как его среднегодовая стоимость. Согласно п.  10 АПК для целей бухгалтерского учета по общему правилу единицей учета основных средств является инвентарный объект.'

In [375]:
aricle_pattern.findall(part)

['105']

In [376]:
aricle_point_pattern.findall(part)

[]

In [377]:
aricle_point_subpoint_pattern.findall(part)

[]

In [185]:
re.search(r'\s?(?:пп\.|подпункту|подпункт|подпунктах)[а-я]*\s*', s1, re.IGNORECASE)

<re.Match object; span=(0, 11), match='подпунктах '>

In [183]:
def extract_letters_smart(text):
    match = re.search(r'\s?(?:пп\.|подпункту|подпункт|подпунктах)[а-я]*\s*', text, re.IGNORECASE)
    if not match:
        return []
    
    between_text = match.group(0)
    
    # Если есть хоть одно слово из 2+ букв (кроме "и") - нахуй
    words = re.findall(r'[а-яa-z]{2,}', between_text, re.IGNORECASE)
    if words and any(word.lower() != 'и' for word in words):
        return []
    
    letters = re.findall(r'[а-яa-z]', between_text, re.IGNORECASE)
    return letters

In [184]:
extract_letters_smart(s1)

[]

In [102]:
before

'хуй пп. 1 п. 1 '

In [120]:
point_pattern = re.compile(r'\s(?:п\.|пункта|пункт)+\s(\d)')
point_pattern.findall(before)

['1']

In [84]:
before

'хуй пп. 1 п. 1 '

In [72]:
after_article

' 374 НК РФ хуйххуйх'

In [66]:
article_number_pattern.

SyntaxError: invalid syntax (2933111671.py, line 1)

In [68]:
article_number_pattern = re.compile(r'\s*[\.\d]+')
article_number_pattern.findall(after_article)[0]

' 374'

In [ ]:
(?:пункт|п|пункта)\.?\s*([\d\w\s,\-\.и]+)

In [50]:
after_article

' 374 НК РФ хуйххуйх'

In [27]:
subpoint_pattern = r'(?:подпункт|подп|пп\.)\s*([а-яё\d,\s\.\-и]+)'
article_pattern = r'(?:статья|ст|статьи)\.?\s*([\d\w\s,\-\.и]+)'
point_pattern = r'(?:пункт|п|пункта)\.?\s*([\d\w\s,\-\.и]+)'

In [34]:
article_pattern = re.compile(r'(?:статья|ст\.|статьи|статье)\s*([\d\w\s,\-\.и]+)')
article_pattern.findall(text)


['374 НК РФ объектами налогообложения признается недвижимое имущество, \nучитываемое на балансе организации в качестве объектов основных средств в порядке, установленном для ст. 105 УК РФ и ведения бухгалтерского учета, в случае, если налоговая база в отношении такого имущества определяется как его среднегодовая стоимость. Согласно п.  10 АПК для целей бухгалтерского учета по общему правилу единицей учета основных средств является инвентарный объект.\n\nСогласно статье 17 Конституции Российской Федерации, каждый гражданин имеет право на жизнь и свободу. Однако, в соответствии с п. 5 ст. 105 УК РФ, убийство двух или более лиц наказывается лишением свободы на срок до двадцати лет. Также, п. 3 ст. 158 УК РФ предусматривает наказание за кражу, совершенную группой лиц по предварительному сговору. Важно отметить, что согласно ст. 30 Гражданского кодекса Российской Федерации, гражданин, признанный недееспособным, не может самостоятельно заключать сделки.\nВ соответствии с пп. 12 п. 4 ст. 159 

In [29]:
subpoint_pattern = re.compile(r'(?:подпункт|подп|пп\.)\s*([а-яё\d,\s\.\-и]+)')
subpoint_pattern.findall(text)



['1 п. 1 ст. 374 ',
 '12 п. 4 ст. 159 ',
 'у 2 пунта б статьи 22 ',
 '4, 5, 6 и 8 п. 1 ст. 14 ',
 '1 п. 2 ст. 34 рандомного кодекса было всё.\n',
 'ах а, б и с пункта 3.345, 23 в статье 66 ']

In [22]:
# text = """
# В пункте 1 статьи 34 Гражданского Кодекса такого не было.
# А в пп. 1 п. 2 ст. 34 рандомного кодекса было всё.
# Таким образом, в подпунктах а, б и с пункта 3.345, 23 в статье 66 НК РФ Ничего такого и не было.
# """


['пп. ', 'пп', 'пп. ', 'подпункт', 'пп. ', 'пп. ', 'подпункт']

In [7]:
ex.extract_links(text)


[LawLink(law_id=None, article='атье', point_article='а', subpoint_article='1'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='п'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='1'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='ст'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='374'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='НК'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='РФ'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='объектам'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='налогообложен'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='я'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='пр'),
 LawLink(law_id=None, article='атье', point_article='а', subpoint_article='знается'),
 LawLink(

In [4]:
law_aliases


{'0': ['Арбитражный процессуальный кодекс Российской Федерации',
  'Арбитражный процессуальный кодекс России',
  'Арбитражный процессуальный кодекс РФ',
  'Арбитражный процессуальный кодекс',
  'АПК России',
  'АПК РФ',
  'АПК'],
 '1': ['Бюджетный кодекс Российской Федерации',
  'Бюджетный кодекс России',
  'Бюджетный кодекс РФ',
  'Бюджетный кодекс',
  'БК России',
  'БК РФ',
  'БК'],
 '2': ['Водный кодекс Российской Федерации',
  'Водный кодекс России',
  'Водный кодекс РФ',
  'Водный кодекс'],
 '3': ['Воздушный кодекс Российской Федерации',
  'Воздушный кодекс России',
  'Воздушный кодекс РФ',
  'Воздушный кодекс'],
 '4': ['Градостроительный кодекс Российской Федерации',
  'Градостроительный кодекс России',
  'Градостроительный кодекс РФ',
  'Градостроительный кодекс'],
 '5': ['Гражданский кодекс Российской Федерации',
  'Гражданский кодекс России',
  'Гражданский кодекс РФ',
  'Гражданский кодекс',
  'ГК РФ',
  'ГК'],
 '6': ['Гражданский процессуальный кодекс Российской Федерации',